In [1]:
import copy
import os
import tempfile
# import unittest

import numpy as np
# import pytest
import torch
from datasets import Dataset
from transformers import AutoModelForCausalLM, AutoTokenizer, TrainingArguments, AutoConfig, LlamaConfig, LlamaForCausalLM

from trl import SFTTrainer
from trl.import_utils import is_peft_available
from trl.trainer import ConstantLengthDataset, DataCollatorForCompletionOnlyLM


tmp_dir = './temp_dir'
# model_id = "trl-internal-testing/dummy-GPT2-correct-vocab"
# model = AutoModelForCausalLM.from_pretrained(model_id)

model_id = 'meta-llama/Meta-Llama-3-8B'
config = AutoConfig.from_pretrained(model_id)
# print(config)
config.intermediate_size = 512
config.hidden_size = 256
config.num_attention_heads = 4
config.num_key_value_heads = 4
config.num_hidden_layers = 1

model = AutoModelForCausalLM.from_config(config)
print(model)
print(model.config)

/Users/denghang/Miniconda3/envs/llm/lib/python3.9/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(128256, 256)
    (layers): ModuleList(
      (0): LlamaDecoderLayer(
        (self_attn): LlamaSdpaAttention(
          (q_proj): Linear(in_features=256, out_features=256, bias=False)
          (k_proj): Linear(in_features=256, out_features=256, bias=False)
          (v_proj): Linear(in_features=256, out_features=256, bias=False)
          (o_proj): Linear(in_features=256, out_features=256, bias=False)
          (rotary_emb): LlamaRotaryEmbedding()
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear(in_features=256, out_features=512, bias=False)
          (up_proj): Linear(in_features=256, out_features=512, bias=False)
          (down_proj): Linear(in_features=512, out_features=256, bias=False)
          (act_fn): SiLU()
        )
        (input_layernorm): LlamaRMSNorm()
        (post_attention_layernorm): LlamaRMSNorm()
      )
    )
    (norm): LlamaRMSNorm()
  )
  (lm_head): Linear(in_features=256, out_features=128256, bias=False)
)

LlamaConfig {
  "_name_or_path": "meta-llama/Meta-Llama-3-8B",
  "architectures": [
    "LlamaForCausalLM"
  ],
  "attention_bias": false,
  "attention_dropout": 0.0,
  "bos_token_id": 128000,
  "eos_token_id": 128001,
  "hidden_act": "silu",
  "hidden_size": 256,
  "initializer_range": 0.02,
  "intermediate_size": 512,
  "max_position_embeddings": 8192,
  "model_type": "llama",
  "num_attention_heads": 4,
  "num_hidden_layers": 1,
  "num_key_value_heads": 4,
  "pretraining_tp": 1,
  "rms_norm_eps": 1e-05,
  "rope_scaling": null,
  "rope_theta": 500000.0,
  "tie_word_embeddings": false,
  "torch_dtype": "bfloat16",
  "transformers_version": "4.38.1",
  "use_cache": true,
  "vocab_size": 128256
}

In [2]:
# tokenizer = AutoTokenizer.from_pretrained(model_id, add_special_tokens=False)
tokenizer = AutoTokenizer.from_pretrained(model_id, padding_side='left')
print(tokenizer)

tokenizer.add_special_tokens({'pad_token': '<|reserved_special_token_0|>'})
print(tokenizer)


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


PreTrainedTokenizerFast(name_or_path='meta-llama/Meta-Llama-3-8B', vocab_size=128000, 
model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='left', truncation_side='right', 
special_tokens={'bos_token': '<|begin_of_text|>', 'eos_token': '<|end_of_text|>'}, 
clean_up_tokenization_spaces=True),  added_tokens_decoder={
        128000: AddedToken("<|begin_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128001: AddedToken("<|end_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128002: AddedToken("<|reserved_special_token_0|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128003: AddedToken("<|reserved_special_token_1|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128004: AddedToken("<|reserved_special_token_2|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128005: AddedToken("<|reserved_special_token_3|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128006: AddedToken("<|start_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128007: AddedToken("<|end_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128008: AddedToken("<|reserved_special_token_4|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128009: AddedToken("<|eot_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128010: AddedToken("<|reserved_special_token_5|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128011: AddedToken("<|reserved_special_token_6|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128012: AddedToken("<|reserved_special_token_7|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128013: AddedToken("<|reserved_special_token_8|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128014: AddedToken("<|reserved_special_token_9|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128015: AddedToken("<|reserved_special_token_10|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128016: AddedToken("<|reserved_special_token_11|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128017: AddedToken("<|reserved_special_token_12|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128018: AddedToken("<|reserved_special_token_13|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128019: AddedToken("<|reserved_special_token_14|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128020: AddedToken("<|reserved_special_token_15|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128021: AddedToken("<|reserved_special_token_16|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128022: AddedToken("<|reserved_special_token_17|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128023: AddedToken("<|reserved_special_token_18|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128024: AddedToken("<|reserved_special_token_19|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128025: AddedToken("<|reserved_special_token_20|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128026: AddedToken("<|reserved_special_token_21|>", rstrip=Fa

PreTrainedTokenizerFast(name_or_path='meta-llama/Meta-Llama-3-8B', vocab_size=128000, 
model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='left', truncation_side='right', 
special_tokens={'bos_token': '<|begin_of_text|>', 'eos_token': '<|end_of_text|>', 'pad_token': 
'<|reserved_special_token_0|>'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
        128000: AddedToken("<|begin_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128001: AddedToken("<|end_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128002: AddedToken("<|reserved_special_token_0|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128003: AddedToken("<|reserved_special_token_1|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128004: AddedToken("<|reserved_special_token_2|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128005: AddedToken("<|reserved_special_token_3|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128006: AddedToken("<|start_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128007: AddedToken("<|end_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128008: AddedToken("<|reserved_special_token_4|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128009: AddedToken("<|eot_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128010: AddedToken("<|reserved_special_token_5|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128011: AddedToken("<|reserved_special_token_6|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128012: AddedToken("<|reserved_special_token_7|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128013: AddedToken("<|reserved_special_token_8|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128014: AddedToken("<|reserved_special_token_9|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128015: AddedToken("<|reserved_special_token_10|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128016: AddedToken("<|reserved_special_token_11|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128017: AddedToken("<|reserved_special_token_12|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128018: AddedToken("<|reserved_special_token_13|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128019: AddedToken("<|reserved_special_token_14|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128020: AddedToken("<|reserved_special_token_15|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128021: AddedToken("<|reserved_special_token_16|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128022: AddedToken("<|reserved_special_token_17|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128023: AddedToken("<|reserved_special_token_18|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128024: AddedToken("<|reserved_special_token_19|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128025: AddedToken("<|reserved_special_token_20|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128026: AddedTok

# 模型增加Pad Token

In [3]:
model.pad_token_id = tokenizer.pad_token_id
model.pad_token = tokenizer.pad_token

print(model)
print(tokenizer)
# print(tokenizer('<unk>', add_special_tokens = False))

LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(128256, 256)
    (layers): ModuleList(
      (0): LlamaDecoderLayer(
        (self_attn): LlamaSdpaAttention(
          (q_proj): Linear(in_features=256, out_features=256, bias=False)
          (k_proj): Linear(in_features=256, out_features=256, bias=False)
          (v_proj): Linear(in_features=256, out_features=256, bias=False)
          (o_proj): Linear(in_features=256, out_features=256, bias=False)
          (rotary_emb): LlamaRotaryEmbedding()
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear(in_features=256, out_features=512, bias=False)
          (up_proj): Linear(in_features=256, out_features=512, bias=False)
          (down_proj): Linear(in_features=512, out_features=256, bias=False)
          (act_fn): SiLU()
        )
        (input_layernorm): LlamaRMSNorm()
        (post_attention_layernorm): LlamaRMSNorm()
      )
    )
    (norm): LlamaRMSNorm()
  )
  (lm_head): Linear(in_features=256, out_features=128256, bias=False)
)

PreTrainedTokenizerFast(name_or_path='meta-llama/Meta-Llama-3-8B', vocab_size=128000, 
model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='left', truncation_side='right', 
special_tokens={'bos_token': '<|begin_of_text|>', 'eos_token': '<|end_of_text|>', 'pad_token': 
'<|reserved_special_token_0|>'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
        128000: AddedToken("<|begin_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128001: AddedToken("<|end_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128002: AddedToken("<|reserved_special_token_0|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128003: AddedToken("<|reserved_special_token_1|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128004: AddedToken("<|reserved_special_token_2|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128005: AddedToken("<|reserved_special_token_3|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128006: AddedToken("<|start_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128007: AddedToken("<|end_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128008: AddedToken("<|reserved_special_token_4|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128009: AddedToken("<|eot_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128010: AddedToken("<|reserved_special_token_5|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128011: AddedToken("<|reserved_special_token_6|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128012: AddedToken("<|reserved_special_token_7|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128013: AddedToken("<|reserved_special_token_8|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128014: AddedToken("<|reserved_special_token_9|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128015: AddedToken("<|reserved_special_token_10|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128016: AddedToken("<|reserved_special_token_11|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128017: AddedToken("<|reserved_special_token_12|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128018: AddedToken("<|reserved_special_token_13|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128019: AddedToken("<|reserved_special_token_14|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128020: AddedToken("<|reserved_special_token_15|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128021: AddedToken("<|reserved_special_token_16|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128022: AddedToken("<|reserved_special_token_17|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128023: AddedToken("<|reserved_special_token_18|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128024: AddedToken("<|reserved_special_token_19|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128025: AddedToken("<|reserved_special_token_20|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128026: AddedTok

# 创建数据集

## 单轮数据

In [4]:
dummy_dataset = Dataset.from_dict(
            {
                "question": [
                    "Does llamas know how to code?",
                    "Does llamas know how to fly?",
                    "Does llamas know how to talk?",
                    "Does llamas know how to code?",
                    "Does llamas know how to fly?",
                    "Does llamas know how to talk?",
                    "Does llamas know how to swim?",
                ],
                "answer": [
                    "Yes, llamas are very good at coding.",
                    "No, llamas can't fly.",
                    "Yes, llamas are very good at talking.",
                    "Yes, llamas are very good at coding.",
                    "No, llamas can't fly.",
                    "Yes, llamas are very good at talking.",
                    "No, llamas can't swim.",
                ],
                # "text": [
                #     "### Question: Does llamas know how to code?\n ### Answer: Yes, llamas are very good at coding.",
                #     "### Question: Does llamas know how to fly?\n ### Answer: No, llamas can't fly.",
                #     "### Question: Does llamas know how to talk?\n ### Answer: Yes, llamas are very good at talking.",
                #     "### Question: Does llamas know how to code?\n ### Answer: Yes, llamas are very good at coding.",
                #     "### Question: Does llamas know how to fly?\n ### Answer: No, llamas can't fly.",
                #     "### Question: Does llamas know how to talk?\n ### Answer: Yes, llamas are very good at talking.",
                #     "### Question: Does llamas know how to swim?\n ### Answer: No, llamas can't swim.",
                # ],
            }
        )

dummy_dataset


Dataset({
│   features: ['question', 'answer'],
│   num_rows: 7
})

# TODO： 多轮数据

# 创建Formating函数

In [5]:
def formatting_prompts_func(example):
    text = f"\n###Question: {example['question']}\n###Answer: {example['answer']} <|end_of_text|>"
    return text


def formatting_prompts_func_batched(example):
    output_text = []
    for i, question in enumerate(example["question"]):
        text = f" \n###Question: {question}\n###Answer: {example['answer'][i]} <|end_of_text|>"
        output_text.append(text)
    return output_text


# 创建collator

In [6]:
training_args = TrainingArguments(
                output_dir=tmp_dir,
                dataloader_drop_last=True,
                evaluation_strategy="no",
                max_steps=512,
                eval_steps=2,
                save_steps=2,
                logging_steps=32,
                per_device_train_batch_size=4,
                learning_rate = 1e-4,
            )

instruction_template = "###Question:"
assistant_template = "###Answer:"

inst_tokenizerd = tokenizer(instruction_template, add_special_tokens=False)
ass_tokenizerd = tokenizer(assistant_template, add_special_tokens=False)

data_collator = DataCollatorForCompletionOnlyLM(
            response_template=ass_tokenizerd['input_ids'][1:],
            tokenizer=tokenizer, mlm=False, pad_to_multiple_of=True)

In [7]:
print(ass_tokenizerd)
print(tokenizer.decode(ass_tokenizerd['input_ids'][0]))
print(tokenizer.decode(ass_tokenizerd['input_ids'][1]))
print(tokenizer.decode(ass_tokenizerd['input_ids'][2]))

{'input_ids': [14711, 16533, 25], 'attention_mask': [1, 1, 1]}

###

Answer

:

# 创建 Trainer

In [8]:
sft_trainer = SFTTrainer(
    model=model,
    args=training_args,
    train_dataset=dummy_dataset,
    data_collator = data_collator,
    max_seq_length=256,  # make sure there is at least 1 packed sequence
    packing=False,
    # dataset_text_field = None,
    formatting_func = formatting_prompts_func_batched,
)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Map:   0%|          | 0/7 [00:00<?, ? examples/s]

# Debug Collator

In [9]:
print(sft_trainer.train_dataset)
print(sft_trainer.data_collator)
# print(tokenizer(assistant_template))

# 之前的版本设置为
batch = data_collator([sft_trainer.train_dataset[0]['input_ids'], sft_trainer.train_dataset[1]['input_ids']])
print(batch)


Dataset({
    features: ['input_ids', 'attention_mask'],
    num_rows: 7
})

DataCollatorForCompletionOnlyLM(
    tokenizer=PreTrainedTokenizerFast(name_or_path='meta-llama/Meta-Llama-3-8B', vocab_size=128000, 
model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='left', truncation_side='right', 
special_tokens={'bos_token': '<|begin_of_text|>', 'eos_token': '<|end_of_text|>', 'pad_token': 
'<|reserved_special_token_0|>'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
        128000: AddedToken("<|begin_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128001: AddedToken("<|end_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128002: AddedToken("<|reserved_special_token_0|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128003: AddedToken("<|reserved_special_token_1|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128004: AddedToken("<|reserved_special_token_2|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128005: AddedToken("<|reserved_special_token_3|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128006: AddedToken("<|start_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128007: AddedToken("<|end_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128008: AddedToken("<|reserved_special_token_4|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128009: AddedToken("<|eot_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128010: AddedToken("<|reserved_special_token_5|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128011: AddedToken("<|reserved_special_token_6|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128012: AddedToken("<|reserved_special_token_7|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128013: AddedToken("<|reserved_special_token_8|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128014: AddedToken("<|reserved_special_token_9|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128015: AddedToken("<|reserved_special_token_10|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128016: AddedToken("<|reserved_special_token_11|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128017: AddedToken("<|reserved_special_token_12|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128018: AddedToken("<|reserved_special_token_13|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128019: AddedToken("<|reserved_special_token_14|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128020: AddedToken("<|reserved_special_token_15|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128021: AddedToken("<|reserved_special_token_16|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128022: AddedToken("<|reserved_special_token_17|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128023: AddedToken("<|reserved_special_token_18|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128024: AddedToken("<|reserved_special_token_19|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128025: AddedToken("<|reserved_special_token_20|>", rstrip=False, lstrip=False, single_word=False, 
normalized

{
    'input_ids': tensor([[128000,    720,  14711,  14924,     25,  12838,   9507,  29189,   1440,
           1268,    311,   2082,   5380,  14711,  16533,     25,   7566,     11,
           9507,  29189,    527,   1633,   1695,    520,  11058,     13,    220,
         128001],
        [128002, 128002, 128000,    720,  14711,  14924,     25,  12838,   9507,
          29189,   1440,   1268,    311,  11722,   5380,  14711,  16533,     25,
           2360,     11,   9507,  29189,    649,    956,  11722,     13,    220,
         128001]]),
    'labels': tensor([[  -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
           -100,   -100,   -100,   -100,   -100,   -100,   -100,   7566,     11,
           9507,  29189,    527,   1633,   1695,    520,  11058,     13,    220,
         128001],
        [  -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
           -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
           2360,     11,   9507,  29189,    649,    956,  11722,     13,    220,
         128001]])
}

In [10]:
print(sft_trainer.train_dataset[0]['attention_mask'])
print(sft_trainer.train_dataset[1]['attention_mask'])

[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]

[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]

In [11]:

print(tokenizer.decode(sft_trainer.train_dataset[0]['input_ids'], skip_special_tokens=False))
print(tokenizer.decode(sft_trainer.train_dataset[1]['input_ids'], skip_special_tokens=False))


<|begin_of_text|> 
###Question: Does llamas know how to code?
###Answer: Yes, llamas are very good at coding. <|end_of_text|>

<|begin_of_text|> 
###Question: Does llamas know how to fly?
###Answer: No, llamas can't fly. <|end_of_text|>

# sft 训练

In [1]:
# sft_trainer.train()

# Llama-3 prompt template

add chat teamplate original from `meta-llama/Meta-Llama-3-8B-Instruct`

you should read Meta Llama3 Official doc 

In [99]:
tokenizer = AutoTokenizer.from_pretrained(model_id, padding_side='left', add_bos_token = False)
print(tokenizer)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


PreTrainedTokenizerFast(name_or_path='meta-llama/Meta-Llama-3-8B', vocab_size=128000, 
model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='left', truncation_side='right', 
special_tokens={'bos_token': '<|begin_of_text|>', 'eos_token': '<|end_of_text|>'}, 
clean_up_tokenization_spaces=True),  added_tokens_decoder={
        128000: AddedToken("<|begin_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128001: AddedToken("<|end_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128002: AddedToken("<|reserved_special_token_0|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128003: AddedToken("<|reserved_special_token_1|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128004: AddedToken("<|reserved_special_token_2|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128005: AddedToken("<|reserved_special_token_3|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128006: AddedToken("<|start_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128007: AddedToken("<|end_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128008: AddedToken("<|reserved_special_token_4|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128009: AddedToken("<|eot_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128010: AddedToken("<|reserved_special_token_5|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128011: AddedToken("<|reserved_special_token_6|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128012: AddedToken("<|reserved_special_token_7|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128013: AddedToken("<|reserved_special_token_8|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128014: AddedToken("<|reserved_special_token_9|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128015: AddedToken("<|reserved_special_token_10|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128016: AddedToken("<|reserved_special_token_11|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128017: AddedToken("<|reserved_special_token_12|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128018: AddedToken("<|reserved_special_token_13|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128019: AddedToken("<|reserved_special_token_14|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128020: AddedToken("<|reserved_special_token_15|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128021: AddedToken("<|reserved_special_token_16|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128022: AddedToken("<|reserved_special_token_17|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128023: AddedToken("<|reserved_special_token_18|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128024: AddedToken("<|reserved_special_token_19|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128025: AddedToken("<|reserved_special_token_20|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128026: AddedToken("<|reserved_special_token_21|>", rstrip=Fa

In [100]:
print(tokenizer.chat_template)
tokenizer.chat_template = '''{% set loop_messages = messages %}{% for message in loop_messages %}{% set content = '<|start_header_id|>' + message['role'] + '<|end_header_id|>\n\n'+ message['content'] | trim + '<|eot_id|>' %}{% if loop.index0 == 0 %}{% set content = bos_token + content %}{% endif %}{{ content }}{% endfor %}{% if add_generation_prompt %}{{ '<|start_header_id|>assistant<|end_header_id|>\n\n' }}{% endif %}'''

None

In [101]:
print(tokenizer.chat_template)

{% set loop_messages = messages %}{% for message in loop_messages %}{% set content = '<|start_header_id|>' + 
message['role'] + '<|end_header_id|>

'+ message['content'] | trim + '<|eot_id|>' %}{% if loop.index0 == 0 %}{% set content = bos_token + content %}{% 
endif %}{{ content }}{% endfor %}{% if add_generation_prompt %}{{ '<|start_header_id|>assistant<|end_header_id|>

' }}{% endif %}

## chat-messages

不使用formatting 函数， 使用官方自带的对话模版

开发会更加简便，特别是涉及到多轮对话的情况

In [102]:
messages = [
    {"role": "system", "content": "you are a robot"},
    {"role": "user", "content": "my question 1 ?"},
    {"role": "assistant", "content": "my answer 1"},
    {"role": "user", "content": "my question 2 ?"},
]

以下使用apply_chat_template方法，比较灵活的转化成string，不建议在这个阶段转成token

In [103]:
str = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=False)
print(str)

<|begin_of_text|><|start_header_id|>system<|end_header_id|>

you are a robot<|eot_id|><|start_header_id|>user<|end_header_id|>

my question 1 ?<|eot_id|><|start_header_id|>assistant<|end_header_id|>

my answer 1<|eot_id|><|start_header_id|>user<|end_header_id|>

my question 2 ?<|eot_id|>

In [104]:
str = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
print(str)
print(type(str))

<|begin_of_text|><|start_header_id|>system<|end_header_id|>

you are a robot<|eot_id|><|start_header_id|>user<|end_header_id|>

my question 1 ?<|eot_id|><|start_header_id|>assistant<|end_header_id|>

my answer 1<|eot_id|><|start_header_id|>user<|end_header_id|>

my question 2 ?<|eot_id|><|start_header_id|>assistant<|end_header_id|>

<class 'str'>

观察token序列

In [105]:
# tokenize=True will return token_ids

# add_generation_prompt set True for inference
token_id = tokenizer.apply_chat_template(messages, tokenize=True, add_generation_prompt=True, return_tensors='pt') 
print(token_id)

# add_generation_prompt set False for training
token_id = tokenizer.apply_chat_template(messages, tokenize=True, add_generation_prompt=False, return_tensors='pt') 
print(token_id)

tensor([[128000, 128006,   9125, 128007,    271,   9514,    527,    264,  12585,
         128009, 128006,    882, 128007,    271,   2465,   3488,    220,     16,
            949, 128009, 128006,  78191, 128007,    271,   2465,   4320,    220,
             16, 128009, 128006,    882, 128007,    271,   2465,   3488,    220,
             17,    949, 128009, 128006,  78191, 128007,    271]])

tensor([[128000, 128006,   9125, 128007,    271,   9514,    527,    264,  12585,
         128009, 128006,    882, 128007,    271,   2465,   3488,    220,     16,
            949, 128009, 128006,  78191, 128007,    271,   2465,   4320,    220,
             16, 128009, 128006,    882, 128007,    271,   2465,   3488,    220,
             17,    949, 128009]])

In [106]:
print(tokenizer('<|begin_of_text|>', add_special_tokens=False))
print(tokenizer('<|start_header_id|>', add_special_tokens=False))
print(tokenizer('<|end_header_id|>', add_special_tokens=False))
print(tokenizer('<|eot_id|>', add_special_tokens=False))
print(tokenizer('<|end_of_text|>', add_special_tokens=False))

{'input_ids': [128000], 'attention_mask': [1]}

{'input_ids': [128006], 'attention_mask': [1]}

{'input_ids': [128007], 'attention_mask': [1]}

{'input_ids': [128009], 'attention_mask': [1]}

{'input_ids': [128001], 'attention_mask': [1]}

In [107]:
print(tokenizer('<|reserved_special_token_0|>', add_special_tokens=False))
print(tokenizer.pad_token_id)
print(tokenizer.pad_token)

# 添加pad token
tokenizer.add_special_tokens({'pad_token': '<|reserved_special_token_0|>'})
print(tokenizer.pad_token_id)
print(tokenizer.pad_token)

{'input_ids': [128002], 'attention_mask': [1]}

None

None

128002

<|reserved_special_token_0|>

# 增加对话

In [108]:
messages = [
    {"role": "system", "content": "you are a robot"},
    {"role": "user", "content": "my question 1 ?"},
    {"role": "assistant", "content": "my answer 1"},
    {"role": "user", "content": "my question 2 ?"},
]

print(messages) # 用于generation

messages.append({"role": "assistant", "content": "my answer 2 ?"})
print(messages) # 用于训练

[
    {'role': 'system', 'content': 'you are a robot'},
    {'role': 'user', 'content': 'my question 1 ?'},
    {'role': 'assistant', 'content': 'my answer 1'},
    {'role': 'user', 'content': 'my question 2 ?'}
]

[
    {'role': 'system', 'content': 'you are a robot'},
    {'role': 'user', 'content': 'my question 1 ?'},
    {'role': 'assistant', 'content': 'my answer 1'},
    {'role': 'user', 'content': 'my question 2 ?'},
    {'role': 'assistant', 'content': 'my answer 2 ?'}
]

In [109]:
print(tokenizer('<|start_head_id|>', add_special_tokens=False))
print(tokenizer('<|end_header_id|>', add_special_tokens=False))
print(tokenizer('user', add_special_tokens=False))
print(tokenizer('assistant', add_special_tokens=False))

{'input_ids': [27, 91, 2527, 13439, 851, 91, 29], 'attention_mask': [1, 1, 1, 1, 1, 1, 1]}

{'input_ids': [128007], 'attention_mask': [1]}

{'input_ids': [882], 'attention_mask': [1]}

{'input_ids': [78191], 'attention_mask': [1]}

用方法一产生的prompt 模版是错误的， 


期望的是

128006,   78191, 128007


128006,   882, 128007

In [110]:

instruction_template = "<|start_head_id|>assistant<|end_header_id|>"
response_template = "<|start_head_id|>user<|end_header_id|>"

inst_tokenizerd = tokenizer(instruction_template, add_special_tokens=False)
response_tokenizerd = tokenizer(response_template, add_special_tokens=False)

data_collator = DataCollatorForCompletionOnlyLM(instruction_template=inst_tokenizerd['input_ids'],
            response_template=response_tokenizerd['input_ids'],
            tokenizer=tokenizer, mlm=False, pad_to_multiple_of=True)

print(data_collator.instruction_template)
print(data_collator.response_template)

[27, 91, 2527, 13439, 851, 91, 29, 78191, 128007]

[27, 91, 2527, 13439, 851, 91, 29, 882, 128007]

In [111]:

my_inst_tokenizerd = [128006, 882, 128007]
my_response_tokenizerd = [128006, 78191, 128007]


data_collator = DataCollatorForCompletionOnlyLM(
             instruction_template=my_inst_tokenizerd,
            response_template= my_response_tokenizerd,
            tokenizer=tokenizer, mlm=False, pad_to_multiple_of=True)

print(data_collator.instruction_template)
print(data_collator.response_template)

# 那么我们有更加鲁棒的token模版


[128006, 882, 128007]

[128006, 78191, 128007]

# 创建dataset


In [112]:
def formatting_prompts_func(example):
    text = tokenizer.apply_chat_template(example['messages'], tokenize=False, add_generation_prompt=False) 
    return text


def formatting_prompts_func_batched(example):
    output_text = []
    for i, messages in enumerate(example['messages']):
        text = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=False)
        output_text.append(text)
    return output_text


In [113]:
messages_1 = [
    {"role": "system", "content": "you are a robot"},
    {"role": "user", "content": "my question 1 ?"},
    {"role": "assistant", "content": "my answer 1"},
    {"role": "user", "content": "my question 2 ?"},
    {"role": "assistant", "content": "hello world "}
]

messages_2 = [
    {"role": "system", "content": "you are a robot"},
    {"role": "user", "content": "my question 1 ?"},
    {"role": "assistant", "content": "my answer 1"},
    {"role": "user", "content": "my question 2 ?"},
    {"role": "assistant", "content": "I love large language models "}
]

# https://huggingface.co/docs/datasets/v1.1.1/loading_datasets.html
from datasets import Dataset
my_dict = {'messages': [messages_1, messages_2]}
dummy_dataset = Dataset.from_dict(my_dict)
print(dummy_dataset)

Dataset({
    features: ['messages'],
    num_rows: 2
})

In [114]:
tokenizer.padding_side = 'left'
# tokenizer.add

In [115]:
training_args = TrainingArguments(
                output_dir=tmp_dir,
                dataloader_drop_last=True,
                evaluation_strategy="no",
                max_steps=512,
                eval_steps=2,
                save_steps=2,
                logging_steps=32,
                per_device_train_batch_size=4,
                learning_rate = 1e-4,
            )
sft_trainer = SFTTrainer(
    model=model,
    args=training_args,
    train_dataset=dummy_dataset,
    data_collator = data_collator,
    max_seq_length=256,  # make sure there is at least 1 packed sequence
    packing=False,
    # dataset_text_field = None,
    formatting_func = formatting_prompts_func_batched,
)

print(sft_trainer.train_dataset)
print(sft_trainer.data_collator)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Map:   0%|          | 0/2 [00:00<?, ? examples/s]

Dataset({
    features: ['input_ids', 'attention_mask'],
    num_rows: 2
})

DataCollatorForCompletionOnlyLM(
    tokenizer=PreTrainedTokenizerFast(name_or_path='meta-llama/Meta-Llama-3-8B', vocab_size=128000, 
model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='left', truncation_side='right', 
special_tokens={'bos_token': '<|begin_of_text|>', 'eos_token': '<|end_of_text|>', 'pad_token': 
'<|reserved_special_token_0|>'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
        128000: AddedToken("<|begin_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128001: AddedToken("<|end_of_text|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128002: AddedToken("<|reserved_special_token_0|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128003: AddedToken("<|reserved_special_token_1|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128004: AddedToken("<|reserved_special_token_2|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128005: AddedToken("<|reserved_special_token_3|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128006: AddedToken("<|start_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128007: AddedToken("<|end_header_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128008: AddedToken("<|reserved_special_token_4|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128009: AddedToken("<|eot_id|>", rstrip=False, lstrip=False, single_word=False, normalized=False, 
special=True),
        128010: AddedToken("<|reserved_special_token_5|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128011: AddedToken("<|reserved_special_token_6|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128012: AddedToken("<|reserved_special_token_7|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128013: AddedToken("<|reserved_special_token_8|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128014: AddedToken("<|reserved_special_token_9|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128015: AddedToken("<|reserved_special_token_10|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128016: AddedToken("<|reserved_special_token_11|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128017: AddedToken("<|reserved_special_token_12|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128018: AddedToken("<|reserved_special_token_13|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128019: AddedToken("<|reserved_special_token_14|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128020: AddedToken("<|reserved_special_token_15|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128021: AddedToken("<|reserved_special_token_16|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128022: AddedToken("<|reserved_special_token_17|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128023: AddedToken("<|reserved_special_token_18|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128024: AddedToken("<|reserved_special_token_19|>", rstrip=False, lstrip=False, single_word=False, 
normalized=False, special=True),
        128025: AddedToken("<|reserved_special_token_20|>", rstrip=False, lstrip=False, single_word=False, 
normalized

In [116]:
batch = data_collator([sft_trainer.train_dataset[0]['input_ids'], sft_trainer.train_dataset[1]['input_ids']])
print(batch)

{
    'input_ids': tensor([[128002, 128002, 128002, 128000, 128000, 128006,   9125, 128007,    271,
           9514,    527,    264,  12585, 128009, 128006,    882, 128007,    271,
           2465,   3488,    220,     16,    949, 128009, 128006,  78191, 128007,
            271,   2465,   4320,    220,     16, 128009, 128006,    882, 128007,
            271,   2465,   3488,    220,     17,    949, 128009, 128006,  78191,
         128007,    271,  15339,   1917, 128009],
        [128000, 128000, 128006,   9125, 128007,    271,   9514,    527,    264,
          12585, 128009, 128006,    882, 128007,    271,   2465,   3488,    220,
             16,    949, 128009, 128006,  78191, 128007,    271,   2465,   4320,
            220,     16, 128009, 128006,    882, 128007,    271,   2465,   3488,
            220,     17,    949, 128009, 128006,  78191, 128007,    271,     40,
           3021,   3544,   4221,   4211, 128009]]),
    'labels': tensor([[  -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
           -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
           -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
            271,   2465,   4320,    220,     16, 128009,   -100,   -100,   -100,
           -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
           -100,    271,  15339,   1917, 128009],
        [  -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
           -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
           -100,   -100,   -100,   -100,   -100,   -100,    271,   2465,   4320,
            220,     16, 128009,   -100,   -100,   -100,   -100,   -100,   -100,
           -100,   -100,   -100,   -100,   -100,   -100,   -100,    271,     40,
           3021,   3544,   4221,   4211, 128009]])
}

In [117]:
label1_1 = [271,   2465,   4320,    220,     16, 128009]
label1_2 = [271,  15339,   1917, 128009]

In [118]:
tokenizer.decode(label1_1)

'\n\nmy answer 1<|eot_id|>'

In [119]:
tokenizer.decode(label1_2)

'\n\nhello world<|eot_id|>'

In [123]:
label2_1 = [271,   2465,   4320, 220,     16, 128009]
label2_2 = [271,     40,   3021,   3544,   4221,   4211, 128009]

In [124]:
tokenizer.decode(label2_1)

'\n\nmy answer 1<|eot_id|>'

In [125]:
tokenizer.decode(label2_2)

'\n\nI love large language models<|eot_id|>'